In [45]:
import pandas as pd
import polars as pl
import datetime as dt
pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)
import numpy as np

In [46]:
import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import _fetch_batch, fetch_data, fetch_spot_data

In [47]:
tb = pd.read_csv('../weekly opt selling positional JJMS/Lobster_1_30.csv')
# tb = tb.drop(columns=['Unnamed: 0'])

In [48]:
tb.tail(500)

Day  Strike      Expiry  DTE Option Type  Entry Price  \
2476  2023-12-29   21950  2024-01-04    6          CE        83.25   
2477  2023-12-29   21500  2024-01-04    6          PE        62.80   
2478  2024-01-01   21950  2024-01-04    3          CE        41.30   
2479  2024-01-01   21500  2024-01-04    3          PE        45.25   
2480  2024-01-02   21950  2024-01-04    2          CE        28.25   
2481  2024-01-02   21550  2024-01-04    2          PE        33.40   
2482  2024-01-03   21900  2024-01-04    1          CE        10.00   
2483  2024-01-03   21450  2024-01-04    1          PE        30.30   
2484  2024-01-04   21800  2024-01-04    0          CE         1.85   
2485  2024-01-04   21400  2024-01-04    0          PE         4.50   
2486  2024-01-05   21900  2024-01-11    6          CE        58.25   
2487  2024-01-05   21500  2024-01-11    6          PE        35.95   
2488  2024-01-08   21950  2024-01-11    3          CE        24.95   
2489  2024-01-08   21550  2024-01-11    3          PE        42.45   
2490  2024-01-09   21850  2024-01-11    2          CE        23.85   
2491  2024-01-09   21450  2024-01-11    2          PE        21.00   
2492  2024-01-10   21750  2024-01-11    1          CE        15.00   
2493  2024-01-10   21300  2024-01-11    1          PE        15.80   
2494  2024-01-11   21900  2024-01-11    0          CE         1.50   
2495  2024-01-11   21450  2024-01-11    0          PE         2.25   
2496  2024-01-12   22000  2024-01-18    6          CE        36.85   
2497  2024-01-12   21550  2024-01-18    6          PE        65.55   
2498  2024-01-15   22250  2024-01-18    3          CE        37.35   
2499  2024-01-15   21850  2024-01-18    3          PE        57.75   
2500  2024-01-16   22300  2024-01-18    2          CE        21.30   
2501  2024-01-16   21850  2024-01-18    2          PE        40.80   
2502  2024-01-17   21850  2024-01-18    1          CE       116.85   
2503  2024-01-17   21450  2024-01-18    1          PE        21.15   
2504  2024-01-18   21650  2024-01-18    0          CE         6.00   
2505  2024-01-18   21200  2024-01-18    0          PE         7.05   
2506  2024-01-19   21850  2024-01-25    6          CE        73.60   
2507  2024-01-19   21400  2024-01-25    6          PE        65.75   
2508  2024-01-20   21900  2024-01-25    5          CE        69.55   
2509  2024-01-20   21500  2024-01-25    5          PE        41.90   
2510  2024-01-23   21950  2024-01-25    2          CE        38.25   
2511  2024-01-23   21500  2024-01-25    2          PE        23.05   
2512  2024-01-24   21400  2024-01-25    1          CE        40.20   
2513  2024-01-24   20950  2024-01-25    1          PE        35.55   
2514  2024-01-25   21650  2024-01-25    0          CE        11.25   
2515  2024-01-25   21250  2024-01-25    0          PE        20.05   
2516  2024-01-29   21650  2024-02-01    3          CE       129.50   
2517  2024-01-29   21200  2024-02-01    3          PE        58.15   
2518  2024-01-30   22000  2024-02-01    2          CE        97.75   
2519  2024-01-30   21550  2024-02-01    2          PE        68.05   
2520  2024-01-31   21700  2024-02-01    1          CE        65.75   
2521  2024-01-31   21250  2024-02-01    1          PE        66.85   
2522  2024-02-01   22000  2024-02-01    0          CE        42.55   
2523  2024-02-01   21550  2024-02-01    0          PE        65.10   
2524  2024-02-02   22050  2024-02-08    6          CE        86.10   
2525  2024-02-02   21600  2024-02-08    6          PE        58.70   
2526  2024-02-05   22150  2024-02-08    3          CE        46.55   
2527  2024-02-05   21700  2024-02-08    3          PE        89.15   
2528  2024-02-06   22050  2024-02-08    2          CE        45.95   
2529  2024-02-06   21600  2024-02-08    2          PE        69.65   
2530  2024-02-07   22250  2024-02-08    1          CE        29.70   
2531  2024-02-07   21800  2024-02-08    1          PE        32.40   
2532  2024-02-08   2225

In [49]:
tb['Entry Time'] = dt.time(9, 15)

In [50]:
# def round_to_nearest_50(value):
#     return int(50 * round(value / 50))

# def get_hedge_pct(margin):
#     if 100 < margin <= 150:
#         return 5
#     elif 150 < margin <= 200:
#         return 4
#     elif 200 < margin < 300:
#         return 3
#     else:
#         return 0  # Default value if margin doesn't fit any range

# async def add_hedges(df):
#     # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
#     # hedge_pct = 2.75
#     index_name = "NIFTY"
#     index_str_for_opt = "nifty"

#     df["Hedge Strike"] = df.apply(
#         lambda row: (
#             int(round_to_nearest_50(row["strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "C" and row["Margin"] > 100
#             else int(round_to_nearest_50(row["strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
#             if row["type"] == "P" and row["Margin"] > 100
#             else 0  # Default value if neither condition matches
#         ),
#         axis=1,
#     )

#     # df["Hedge Contract"] = df.apply(
#     #     lambda row: get_option_contract_name2(
#     #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
#     #     ),
#     #     axis=1,
#     # )

#     df["Hedge Entry Price"] = np.nan
#     df["Hedge Exit Price"] = np.nan

#     # print(df['Hedge Strike'].to_string())

#     for i in range(0, len(df)):
#         print(df.iloc[i]['date'])
#         if df.iloc[i]['Hedge Strike']:
#             # print(df.iloc[i]["Week"])
#             entry_date = df.iloc[i]['date']
#             entry_time = df.iloc[i]['Entry Time']
#             exit_date = df.iloc[i]['Exit date']
#             exit_time = df.iloc[i]['Exit Time']
#             hedge_strike = int(df.iloc[i]["Hedge Strike"])
#             hedge_expiry = df.iloc[i]["expiry"]
#             hedge_opt_type = df.iloc[i]["type"]
#             # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
#             # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
#             hedge_df = await fetch_data(
#                 index=index_str_for_opt,
#                 start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
#                 end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
#                 start_time=dt.datetime.strptime(entry_time, "%H:%M:%S").time(),
#                 end_time=dt.datetime.strptime(exit_time, "%H:%M:%S").time(),
#                 expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
#                 strike=hedge_strike,
#                 asset_class=hedge_opt_type,
#             )
#             if not isinstance(hedge_df, str) and hedge_df is not None:
#                 hedge_df = hedge_df.to_pandas()
#             else:
#                 print(hedge_df)
#                 df.loc[i, "Hedge Entry Price"] = 0
#                 df.loc[i, "Hedge Exit Price"] = 0
#                 continue
#             # print(hedge_df)
    
#             hedge_entry_price = hedge_df.iloc[0]["c"]
#             hedge_exit_price = hedge_df.iloc[-1]["c"]
    
#             print(hedge_entry_price, hedge_exit_price)
    
#             df.loc[i, "Hedge Entry Price"] = hedge_entry_price
#             df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
#     return df

In [51]:
def round_to_nearest_50(value):
    return int(50 * round(value / 50))

def get_hedge_pct(margin):
    if 100 < margin <= 150:
        return 4
    elif 150 < margin <= 200:
        return 3
    elif 200 < margin < 300:
        return 2
    else:
        return 0  # Default value if margin doesn't fit any range

async def add_hedges(df):
    # df.drop(columns=['ROI%', 'Trade Year'], inplace=True)
    # hedge_pct = 2.75
    index_name = "NIFTY"
    index_str_for_opt = "nifty"

    df["Hedge Strike"] = df.apply(
        lambda row: (
            int(round_to_nearest_50(row["Strike"] * (1 + (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "CE" and row["Margin"] > 100
            else int(round_to_nearest_50(row["Strike"] * (1 - (get_hedge_pct(row["Margin"]) / 100))))
            if row["Option Type"] == "PE" and row["Margin"] > 100
            else 0  # Default value if neither condition matches
        ),
        axis=1,
    )

    # df["Hedge Contract"] = df.apply(
    #     lambda row: get_option_contract_name2(
    #         index_name, row["Hedge Strike"], row["Expiry"], row["Option Type"]
    #     ),
    #     axis=1,
    # )

    df["Hedge Entry Price"] = np.nan
    df["Hedge Exit Price"] = np.nan

    # print(df['Hedge Strike'].to_string())

    for i in range(0, len(df)):
        print(df.iloc[i]['Day'])
        if df.iloc[i]['Hedge Strike']:
            # print(df.iloc[i]["Week"])
            entry_date = df.iloc[i]['Day']
            entry_time = df.iloc[i]['Entry Time']
            exit_date = df.iloc[i]['Day']
            exit_time = pd.to_datetime(df.iloc[i]['Exit Time']).time()
            hedge_strike = int(df.iloc[i]["Hedge Strike"])
            hedge_expiry = df.iloc[i]["Expiry"]
            hedge_opt_type = df.iloc[i]["Option Type"]
            # hedge_entry_datetime = dt.datetime.combine(entry_date, entry_time)
            # hedge_exit_datetime = dt.datetime.combine(exit_date, exit_time)
    
            hedge_df = await fetch_data(
                index=index_str_for_opt,
                start_date=dt.datetime.strptime(entry_date, "%Y-%m-%d").date(),
                end_date=dt.datetime.strptime(exit_date, "%Y-%m-%d").date(),
                start_time=entry_time,
                end_time=exit_time,
                expiry=dt.datetime.strptime(hedge_expiry, "%Y-%m-%d"),
                strike=hedge_strike,
                asset_class=hedge_opt_type[:1],
            )
            if not isinstance(hedge_df, str) and hedge_df is not None:
                hedge_df = hedge_df.to_pandas()
            else:
                print(hedge_df)
                df.loc[i, "Hedge Entry Price"] = 0
                df.loc[i, "Hedge Exit Price"] = 0
                continue
            # print(hedge_df)
    
            hedge_entry_price = hedge_df.iloc[0]["c"]
            hedge_exit_price = hedge_df.iloc[-1]["c"]
    
            print(hedge_entry_price, hedge_exit_price)
    
            df.loc[i, "Hedge Entry Price"] = hedge_entry_price
            df.loc[i, "Hedge Exit Price"] = hedge_exit_price
    
    return df

In [52]:
tb_with_hedge = await add_hedges(tb)
# tb_with_hedge.tail()

2019-01-01
2019-01-01
2019-01-02
2019-01-02
2019-01-03
2019-01-03
2019-01-04
2019-01-04
2019-01-07
2019-01-07
2019-01-08
2019-01-08
2019-01-09
2019-01-09
2019-01-10
2019-01-10
2019-01-11
2019-01-11
2019-01-14
2019-01-14
2019-01-15
2019-01-15
2019-01-16
2019-01-16
2019-01-17
2019-01-17
2019-01-18
2019-01-18
2019-01-21
2019-01-21
2019-01-22
2019-01-22
2019-01-23
2019-01-23
2019-01-24
2019-01-24
2019-01-25
1.8 1.7
2019-01-25
6.2 9.4
2019-01-28
4.45 3.2
2019-01-28
6.7 8.8
2019-01-29
5.2 7.25
2019-01-29
7.9 3.35
2019-01-30
1.95 0.75
2019-01-30
2.4 2.8
2019-01-31
0.1 0.15
2019-01-31
0.2 0.05
2019-02-01
2019-02-01
2019-02-04
2019-02-04
2019-02-05
2019-02-05
2019-02-06
2019-02-06
2019-02-07
2019-02-07
2019-02-08
2019-02-08
2019-02-11
1.5 1.0
2019-02-11
7.0 2.0
2019-02-12
0.95 1.0
2019-02-12
1.25 1.5
2019-02-13
0.65 0.35
2019-02-13
0.8 0.95
2019-02-14
0.05 0.05
2019-02-14
0.2 0.15
2019-02-15
2.4 2.25
2019-02-15
7.0 7.7
2019-02-18
3.65 1.25
2019-02-18
14.9 18.45
2019-02-19
2.15 2.5
2019-02-19
8.

In [53]:
tb_with_hedge['Hedge Points'] = tb_with_hedge['Hedge Exit Price'] - tb_with_hedge['Hedge Entry Price']
tb_with_hedge['Hedge PnL'] = tb_with_hedge['Hedge Points'] * tb_with_hedge['Qty']
tb_with_hedge['Hedge ROI%'] = tb_with_hedge.apply(
    lambda row: (row['Hedge PnL'] * 100 / 1000000) if not pd.isna(row['Hedge Points']) else 0,
    axis=1
)
tb_with_hedge['Total ROI%'] = tb_with_hedge['ROI%'] + tb_with_hedge['Hedge ROI%']

In [54]:
tb_with_hedge['Total ROI%'].sum()

720.4639720298666

In [55]:
tb_with_hedge.tail(50)

Day  Strike      Expiry  DTE Option Type  Entry Price  \
2926  2024-11-26   24600  2024-11-28    2          CE        27.35   
2927  2024-11-26   24100  2024-11-28    2          PE        66.10   
2928  2024-11-27   24450  2024-11-28    1          CE        21.75   
2929  2024-11-27   23950  2024-11-28    1          PE        30.45   
2930  2024-11-28   24500  2024-11-28    0          CE        13.15   
2931  2024-11-28   24050  2024-11-28    0          PE         9.90   
2932  2024-11-29   24150  2024-12-05    6          CE       127.45   
2933  2024-11-29   23700  2024-12-05    6          PE        75.95   
2934  2024-12-02   24400  2024-12-05    3          CE        42.85   
2935  2024-12-02   23900  2024-12-05    3          PE        86.65   
2936  2024-12-03   24600  2024-12-05    2          CE        45.45   
2937  2024-12-03   24100  2024-12-05    2          PE        73.55   
2938  2024-12-04   24750  2024-12-05    1          CE        23.50   
2939  2024-12-04   24250  2024-12-05    1          PE        65.10   
2940  2024-12-05   24800  2024-12-05    0          CE        14.25   
2941  2024-12-05   24300  2024-12-05    0          PE        49.60   
2942  2024-12-06   25000  2024-12-12    6          CE       105.05   
2943  2024-12-06   24500  2024-12-12    6          PE       153.80   
2944  2024-12-09   24900  2024-12-12    3          CE        81.05   
2945  2024-12-09   24400  2024-12-12    3          PE        84.80   
2946  2024-12-10   24900  2024-12-12    2          CE        47.80   
2947  2024-12-10   24400  2024-12-12    2          PE        58.35   
2948  2024-12-11   24850  2024-12-12    1          CE        29.45   
2949  2024-12-11   24350  2024-12-12    1          PE        26.40   
2950  2024-12-12   24850  2024-12-12    0          CE         8.90   
2951  2024-12-12   24350  2024-12-12    0          PE         7.00   
2952  2024-12-13   24750  2024-12-19    6          CE        77.25   
2953  2024-12-13   24250  2024-12-19    6          PE        71.25   
2954  2024-12-16   25000  2024-12-19    3          CE        46.10   
2955  2024-12-16   24500  2024-12-19    3          PE        59.40   
2956  2024-12-17   24850  2024-12-19    2          CE        62.70   
2957  2024-12-17   24350  2024-12-19    2          PE        64.35   
2958  2024-12-18   24550  2024-12-19    1          CE        45.50   
2959  2024-12-18   24050  2024-12-19    1          PE        29.80   
2960  2024-12-19   24100  2024-12-19    0          CE        32.90   
2961  2024-12-19   23650  2024-12-19    0          PE        33.50   
2962  2024-12-20   24200  2024-12-26    6          CE       108.15   
2963  2024-12-20   23700  2024-12-26    6          PE       111.20   
2964  2024-12-23   24000  2024-12-26    3          CE        78.15   
2965  2024-12-23   23500  2024-12-26    3          PE        63.45   
2966  2024-12-24   24000  2024-12-26    2          CE        21.35   
2967  2024-12-24   23550  2024-12-26    2          PE        21.90   
2968  2024-12-26   24000  2024-12-26    0          CE        14.60   
2969  2024-12-26   23550  2024-12-26    0          PE        11.35   
2970  2024-12-27   24050  2025-01-02    6          CE          NaN   
2971  2024-12-27   23550  2025-01-02    6          PE          NaN   
2972  2024-12-30   24050  2025-01-02    3          CE          NaN   
2973  2024-12-30   23550  2025-01-02    3          PE          NaN   
2974  2024-12-31   23800  2025-01-02    2          CE          NaN   
2975  2024-12-31   23300  2025-01-02    2          PE          NaN   

      Initial SL  Exit Price            Exit Time  Max Price After Entry  \
2926      35.555      35.555  2024-11-26 09:22:00                  38.75   
2927      85.930      85.930  2024-11-26 10:16:00                 104.75   
2928      28.275      28.275  2024-11-27 12:21:00                  51.30   
2929      39.585       5.850  2024-11-27 15:30:00                  28.35   
2930      17.095      17.095  2024-11-28 09:51:00             

In [56]:
def generate_stats(tb_expiry, ema_window):
    stats_df8 = pd.DataFrame(
        index=range(2019, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe

    # Iterate over each year
    for year in range(2019, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

        # Calculate total ROI
        total_roi = year_trades["Total ROI%"].sum()

        # Calculate total number of trades
        total_trades = len(year_trades)

        # Calculate win rate
        win_rate = (year_trades["Total ROI%"] > 0).mean() * 100

        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["Total ROI%"] > 0]["Total ROI%"].mean()

        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["Total ROI%"] < 0]["Total ROI%"].mean()

        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["Total ROI%"].cumsum() - year_trades["Total ROI%"].cumsum().cummax()
        ).min()

        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        variation = f"{ema_window}"

        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            variation,
        ]

    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["Total ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["Total ROI%"] > 0][
        "Total ROI%"
    ].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["Total ROI%"] < 0]["Total ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["Total ROI%"].cumsum()
        - combined_df_sorted["Total ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    overall_variation = variation

    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        overall_variation,
    ]
    return {overall_roi_dd_ratio: stats_df8}

In [64]:
stats = generate_stats(tb, 'Lobster W Hedges')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2019      99.732019          490   41.22449              1.650283   
2020     186.488032          504  47.420635               2.25308   
2021     155.324984          496  48.185484              1.829255   
2022     107.461373          496  47.580645              1.875618   
2023      64.472922          492  47.764228              0.978474   
2024     106.984642          498  43.172691               1.62941   
Overall  720.463972         2976  45.900538              1.707135   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio         Variation  
2019              -0.989937   -13.510611     7.381755  Lobster W Hedges  
2020              -1.348652   -13.698995    13.613264  Lobster W Hedges  
2021              -1.114099   -14.555113    10.671506  Lobster W Hedges  
2022              -1.299165   -12.413204     8.657021  Lobster W Hedges  
2023              -0.675382    -8.127135     7.933044  Lobster W Hedges  
2024              -0.939531   -10.514631    10.174836  Lobster W Hedges  
Overall           -1.065795   -14.555113    49.499029  Lobster W Hedges

In [61]:
# import pandas as pd

# df = pd.DataFrame(tb_with_hedge)

# cols = df.columns.tolist()

# # Move 'Cumulative ROI%', 'Max Cumulative ROI%' and 'DD' to the last
# desired_cols = ['Cumulative ROI%', 'Max Cumulative ROI%', 'DD']
# cols = [col for col in cols if col not in desired_cols] + desired_cols
# # Reassign the columns to the DataFrame
# df = df[cols]

# df


In [43]:
tb = tb_with_hedge
tb['Cumulative ROI%'] = tb['Total ROI%'].cumsum()
tb['Max Cumulative ROI%'] = tb['Cumulative ROI%'].cummax()  # Maximum value so far
tb['DD'] = tb['Cumulative ROI%'] - tb['Max Cumulative ROI%']  # Drawdown
tb

Day  Strike      Expiry  DTE Option Type  Entry Price  \
0     2017-01-02    8300  2017-01-05    3          CE          NaN   
1     2017-01-02    8150  2017-01-05    3          PE          NaN   
2     2017-01-03    8300  2017-01-05    2          CE          NaN   
3     2017-01-03    8100  2017-01-05    2          PE          NaN   
4     2017-01-04    8300  2017-01-05    1          CE          NaN   
5     2017-01-04    8100  2017-01-05    1          PE          NaN   
6     2017-01-05    8300  2017-01-05    0          CE          NaN   
7     2017-01-05    8150  2017-01-05    0          PE          NaN   
8     2017-01-06    8350  2017-01-12    6          CE          NaN   
9     2017-01-06    8200  2017-01-12    6          PE          NaN   
10    2017-01-09    8350  2017-01-12    3          CE          NaN   
11    2017-01-09    8200  2017-01-12    3          PE          NaN   
12    2017-01-10    8350  2017-01-12    2          CE          NaN   
13    2017-01-10    8200  2017-01-12    2          PE          NaN   
14    2017-01-11    8400  2017-01-12    1          CE          NaN   
15    2017-01-11    8250  2017-01-12    1          PE          NaN   
16    2017-01-12    8450  2017-01-12    0          CE          NaN   
17    2017-01-12    8300  2017-01-12    0          PE          NaN   
18    2017-01-13    8550  2017-01-19    6          CE          NaN   
19    2017-01-13    8350  2017-01-19    6          PE          NaN   
20    2017-01-16    8450  2017-01-19    3          CE          NaN   
21    2017-01-16    8300  2017-01-19    3          PE          NaN   
22    2017-01-17    8500  2017-01-19    2          CE          NaN   
23    2017-01-17    8350  2017-01-19    2          PE          NaN   
24    2017-01-18    8500  2017-01-19    1          CE          NaN   
25    2017-01-18    8300  2017-01-19    1          PE          NaN   
26    2017-01-19    8500  2017-01-19    0          CE          NaN   
27    2017-01-19    8350  2017-01-19    0          PE          NaN   
28    2017-01-20    8500  2017-01-25    5          CE        13.65   
29    2017-01-20    8300  2017-01-25    5          PE        14.90   
30    2017-01-23    8400  2017-01-25    2          CE        20.60   
31    2017-01-23    8250  2017-01-25    2          PE        13.85   
32    2017-01-24    8500  2017-01-25    1          CE         5.75   
33    2017-01-24    8300  2017-01-25    1          PE         3.20   
34    2017-01-25    8600  2017-01-25    0          CE         0.45   
35    2017-01-25    8400  2017-01-25    0          PE         1.10   
36    2017-01-27    8700  2017-02-02    6          CE          NaN   
37    2017-01-27    8500  2017-02-02    6          PE          NaN   
38    2017-01-30    8700  2017-02-02    3          CE          NaN   
39    2017-01-30    8550  2017-02-02    3          PE          NaN   
40    2017-01-31    8700  2017-02-02    2          CE          NaN   
41    2017-01-31    8550  2017-02-02    2          PE          NaN   
42    2017-02-01    8650  2017-02-02    1          CE          NaN   
43    2017-02-01    8500  2017-02-02    1          PE          NaN   
44    2017-02-02    8800  2017-02-02    0          CE          NaN   
45    2017-02-02    8650  2017-02-02    0          PE          NaN   
46    2017-02-03    8800  2017-02-09    6          CE          NaN   
47    2017-02-03    8650  2017-02-09    6          PE          NaN   
48    2017-02-06    8850  2017-02-09    3          CE          NaN   
49    2017-02-06    8700  2017-02-09    3          PE          NaN   
50    2017-02-07    8900  2017-02-09    2          CE          NaN   
51    2017-02-07    8700  2017-02-09    2          PE          NaN   
52    2017-02-08    8850  2017-02-09    1          CE          NaN   
53    2017-02-08    8700  2017-02-09    1          PE          NaN   
54    2017-02-09    8900  2017-02-09    0          CE          NaN   
55    2017-02-09    8700  2017-02-09    0          PE          NaN   
56    2017-02-10    890

In [60]:
# tb = tb.drop(columns=['RSI on Entry', 'day'])

In [59]:
tb.to_csv('Lobster_1_30_w_hedges.csv', index=False)

In [70]:
import pandas as pd

def calculate_dte_stats(df):
    """
    Calculate stats grouped by DTE: 
    - Returns Sum for each DTE
    - Max Drawdown (DD) for each DTE
    - Ratio of Returns Sum to Max DD for each DTE

    Parameters:
        df (pd.DataFrame): DataFrame containing a 'DTE' column, 'returns', and 'drawdown' columns.
    
    Returns:
        pd.DataFrame: DataFrame with aggregated statistics by DTE.
    """
    if 'DTE' not in df.columns or 'Total ROI%' not in df.columns or 'DD' not in df.columns:
        raise ValueError("DataFrame must contain 'DTE', 'returns', and 'drawdown' columns.")
    
    # Group by DTE and calculate required stats
    grouped_stats = df.groupby('DTE').agg(
        returns_sum=('Total ROI%', 'sum'),
        max_drawdown=('DD', 'max')  # Assuming 'drawdown' contains negative values
    ).reset_index()
    
    # Calculate ratio of returns sum to max drawdown
    grouped_stats['returns_to_max_dd_ratio'] = (
        grouped_stats['returns_sum'] / grouped_stats['max_drawdown'].abs()
    )

    return grouped_stats


In [71]:
stats_dte = calculate_dte_stats(tb)

ValueError: DataFrame must contain 'DTE', 'returns', and 'drawdown' columns.